In [77]:
from openai import OpenAI
import json
from dotenv import load_dotenv
import os
import pandas as pd
import numpy as np
import re




In [78]:
# 각자의 Ctee 폴더 경로
my_dir = '/home/wooksbaby/boostcamp6th/'

In [79]:
items_df = pd.read_json(my_dir + "20240308-data/items.json")  # 콘텐츠
events_df = pd.read_json(my_dir + "20240308-data/event_projects.json")  # 행사/이벤트
cats_df = pd.read_json(my_dir + "20240219-data/categories_events.json")  # 이벤트 분류기준
stores_df = pd.read_json(my_dir + "20240219-data/stores.json")  # 크리에이터 스토어

funnels_df = pd.read_json(my_dir + "20240221-data/funnels.json")  # 유입경로
orders_df = pd.read_json(my_dir + "20240308-data/orders_items.json")  # 구매데이터
subs_df = pd.read_json(my_dir + "20240221-data/user_subscribes.json")  # 구독정보


In [80]:
items_df.columns

Index(['id', 'store_id', 'simple_contents', 'content', 'story',
       'product_category_type', 'currency_code', 'price', 'discount_price',
       'discount_started_at', 'discount_ended_at', 'is_adult', 'order_number',
       'sales_count', 'view_count', 'comment_count', 'created_at',
       'updated_at'],
      dtype='object')

In [81]:
stores_df.columns

Index(['id', 'title', 'content', 'alias', 'view_count', 'sales_volume',
       'donation_count', 'created_at', 'updated_at'],
      dtype='object')

In [82]:
# stores_df.rename(columns = {'id': 'store_id'}, inplace=True)

In [83]:
items_df = items_df.drop_duplicates()
stores_df = stores_df.drop_duplicates()
events_df = events_df.drop_duplicates()

In [84]:
def append_item_to_file(item, file_path):
    with open(file_path, 'r+', encoding='utf-8') as f:
        f.seek(0, os.SEEK_END)  # 파일의 끝으로 이동
        position = f.tell()
        if position > 1:
            # 파일이 비어있지 않으면, 마지막 ']'를 제거하고 ',' 추가
            f.seek(position - 1)
            f.write(', ')
        json.dump(item, f, ensure_ascii=False)
        f.write(']')  # JSON 배열을 닫음

In [85]:
# events_df

In [86]:
def remove_html_tags(text):
    if pd.isna(text) or text is None:  # NaN 또는 None 체크
        return text
    
    clean_text = re.sub(r'<.*?>', '', text)  # HTML 태그 제거
    return clean_text

In [87]:
items_df['story']=items_df['story'].apply(remove_html_tags)
events_df['story']=events_df['story'].apply(remove_html_tags)

In [88]:
selected_items_df = items_df[["id", "store_id", "simple_contents", "content", "story"]]
selected_stores_df = stores_df[["id", "title", "content", "alias"]]
selected_events_df = events_df[["id", "store_id", "title", "simple_description", "story"]]

In [89]:
# `items_df`의 컬럼 이름 변경
selected_items_df = selected_items_df.rename(columns={
    'id': 'item_id',
    'simple_contents': 'item_simple_contents',
    'content': 'item_content',
    'story': 'item_story'
})

# `stores_df`의 컬럼 이름 변경 (오타 수정: `selected_items_df` -> `stores_df`)
selected_stores_df = selected_stores_df.rename(columns={
    'id': 'store_id',
    'title': 'store_title',
    'content': 'store_content',
    'alias': 'store_alias'
})

# `events_df`에서 필요한 컬럼 선택 및 컬럼 이름 변경
selected_events_df = selected_events_df.rename(columns={
    'id': 'event_id',
    'title': 'event_title',
    'simple_description': 'event_simple_description',
    'story': 'event_story'
})


In [90]:
selected_items_df['combined_contents'] = selected_items_df.apply(lambda row: f"{row['item_simple_contents']}{row['item_content']}{row['item_story']}", axis=1)
selected_items_df= selected_items_df.drop(['item_simple_contents', 'item_content','item_story'], axis=1)

In [91]:
grouped_items = selected_items_df.groupby('store_id')
specific_store_df = grouped_items.get_group(10)
specific_store_df


item_id  store_id                                  combined_contents
14       30        10  None안녕하세요, BJ&유튜버 양경민입니다 :)\n\n저는 아프리카TV와 유튜브를...
15       31        10  None안녕하세요, BJ&유튜버 양경민입니다 :)\n\n저는 아프리카TV와 유튜브를...
16       32        10  None안녕하세요, BJ&유튜버 양경민입니다 :)\n\n저는 아프리카TV와 유튜브를...
17       33        10  None안녕하세요, BJ&유튜버 양경민입니다 :)\n\n저는 아프리카TV와 유튜브를...
18       34        10  None안녕하세요, BJ&유튜버 양경민입니다 :)\n\n저는 아프리카TV와 유튜브를...
19       35        10  None[상품소개]\n양경민의 아프리카 방송에 참여하고 싶은 분들을 위해\n방송에 ...

In [92]:
grouped_events = selected_events_df.groupby('store_id')


In [93]:
# OpenAI API 키 설정
load_dotenv()

client = OpenAI(
  organization=os.getenv('ORGANIZATION'),
  api_key=os.getenv('OPENAI_API_KEY'),
)


In [94]:
def initialize_file(file_path):
    """지정된 경로의 파일을 열고 빈 JSON 배열로 초기화합니다."""
    with open(file_path, 'w', encoding='utf-8') as f:
        json.dump([], f, ensure_ascii=False, indent=4)



In [95]:
def append_json_list(new_data, file_path):
    """파일에 JSON 데이터를 추가합니다. 데이터가 딕셔너리든 리스트든 처리합니다."""
    try:
        # 파일 내용을 읽고 마지막에 데이터를 추가합니다.
        with open(file_path, 'r', encoding='utf-8') as file:
            try:
                file_data = json.load(file)
                if not isinstance(file_data, list):  # 파일 데이터가 리스트가 아닌 경우
                    file_data = []
            except json.JSONDecodeError:  # 파일이 비어있거나 유효하지 않은 경우
                file_data = []

        # 새 데이터 추가
        if isinstance(new_data, dict):  # 단일 딕셔너리 객체인 경우
            file_data.append(new_data)
        elif isinstance(new_data, list):  # 리스트인 경우
            file_data.extend(new_data)
        
        # 수정된 데이터로 파일을 다시 씁니다.
        with open(file_path, 'w', encoding='utf-8') as file:
            json.dump(file_data, file, ensure_ascii=False, indent=4)
    
    except IOError as e:
        print(f"파일 쓰기 중 오류 발생: {e}")
        

# # 파일 초기화
# initialize_file("your_file_store.json")
# data1 = {"id": 3, "tags": "#그림 #스피드페인팅 #유튜버 #그림컨셉"}
# data2 = {"id": 4, "tags": "#그림 #스피드페인팅 #유튜버 #그림컨셉"}
# data3 = {"id": 5, "tags": "#그림 #스피드페인팅 #유튜버 #그림컨셉"}
# data4 = {"id": 6, "tags": "#그림 #스피드페인팅 #유튜버 #그림컨셉"}
# data5 = [{"id": 7, "tags": "#그림 #스피드페인팅 #유튜버 #그림컨셉"}]

# # 데이터 추가
# append_json_list(data1, "your_file_store.json")
# append_json_list(data2, "your_file_store.json")
# append_json_list(data3, "your_file_store.json")
# append_json_list(data4, "your_file_store.json")
# append_json_list(data5, "your_file_store.json")


In [96]:
def process_json_string(data):
    json_data = json.load(data)
    json_str = str(json_data)
    
    # 시작이 '['로, 마지막이 ']'로 끝나는지 확인합니다.
    if json_str.startswith('[') and json_str.endswith(']'):
        # 시작과 끝의 '['와 ']'를 제거합니다.
        processed_str = json_str[1:-1]
    else:
        # 시작과 끝이 '['와 ']'로 끝나지 않는 경우, 원본 문자열을 사용합니다.
        processed_str = json_str
    
    # 결과 문자열에 ','를 추가합니다.
    processed_str += ','
    return processed_str

In [97]:
def finalize_file(file_path):
    with open(file_path, 'rb+') as f:
        f.seek(-1, os.SEEK_END)  # 파일의 마지막 바이트로 이동
        if f.read(1) == b',':  # 마지막 문자가 ','인 경우
            f.seek(-1, os.SEEK_END)  # ','를 제거하기 위해 다시 이동
            f.truncate()  # 마지막 ',' 제거
        f.write(b']')  # JSON 배열 닫기

In [98]:
def tag_maker(store_id, value):
    """상점과 상품 정보를 분석하여, 각 store_id과 items_id에 해당하는 태그를 생성하고 텍스트데이터와 생성된 태그 정보를 바탕으로 카테고리를 생성해. 태그와 카테고리 생성 시 다음 규칙을 엄격히 준수해:
    1. 모든 태그는 '#태그명' 카테고리는 '카테고리명' 형식으로 제공해.
    2. 카테고리는 store나 item 데이터에 카테고리로 나눌수 있는 정보가있는 꼭 확인해! 카테고리는 여러개를 선택할 수 있어 끝까지 꼭 확인해 특히 성인물 있을수있으니 엄격히 관리해
      ```````````````````````
        디지털 템플릿,
        미술 ∙ 디자인,
        사진 ∙ 영상,
        뷰티 ∙ 패션,
        요리 ∙ 베이킹,
        영화 ∙ 애니 ∙ 방송,
        음악 ∙ 춤 ∙ 엔터테인먼트,
        건강 ∙ 스포츠,
        게임 ∙ e스포츠,
        글쓰기,
        인테리어,
        타로 ∙ 사주 ∙ 관상,
        심리 ∙ 상담,
        교육 ∙ 학습,
        IT ∙ 개발,
        자기계발 ∙ 커리어,
        금융 ∙ 재테크,
        청소년 ∙ 유아,
        반려동물,
        일상 ∙ 소통,
        추천 ∙ 리뷰,
        광고 ∙ 섭외,
        ASMR,
        디지털 템플릿,
        전자책,
        웹화보,
        기타
        ````````````````````````````
    3. 할인, 커미션, 동사, 너무긴 테그는 단어가 아닌 태그는 테그에서 제외해. 카테고리는 스토어와 아이템 전체적으로 파악해서 판단하고 잘모르겠으면 기타로 판단해
    4. 태그와 카테고리는 연관성이 높은순서로 제공해.
    5. 태그명은 꼭 #을붙여서 표현해.
    6. 태그는 명사 형태로 제공되며 태그는 5개를 만들어. 카테고리는 다양할 수 있어.
    7. 'items' 항목에 빈 객체가 포함되어서는 안 됩니다. 모든 아이템은 꼭!!! 'item_id'와 'tags''category' 필드를 가져야 합니다. 또한 형식은 "item_id", "tags"를 key로 가지는 "items": [{"item_id": item_id , "tags":"#tag1#tag2...", "category": 카테고리명 }, {"item_id": item_id, "tags":"#tag1#tag2...","category": 카테고리,카테고리,카테고리...  }, ... , {"item_id": item_id, "tags":"#tag1#tag2...","category": 카테고리,카테고리,카테고리...  }] 형식
    8. 'store' 항목은 스토어에 포함된 item들의 내용을 반영한 태그를 꼭 !!!"store_id", "tags"'category'를 가지는 "store": {, "tags":"#tag1#tag2 ...", "category": 카테고리명  } 형식 으로 저장해야한다 .
    9. 모든 정보는 전체적으로 한국어로 제공되며, JSON 객체는 유효한 형식을 따라야 합니다.
    10.  아이템의 테그가 빈출력이되면 스토어의 테그와 기존의 아이템의 테그를 참고해서 다시 테그를 만들어

    """
    try:

        completion = client.chat.completions.create(
            model="gpt-3.5-turbo-0125",
            messages=[
                {
                    "role": "system",
                    "content": """상점(store)과 상품(items) 정보를 분석하여 각각의 store_id와 item_id에 해당하는 태그를 생성하고, 이 정보와 생성된 태그를 바탕으로 카테고리를 결정하는 작업입니다. 작업을 수행하기 전에, 다음 규칙을 엄격히 준수해야 합니다:

1. 모든 태그는 '#태그명' 형식으로 제공해야 합니다. 예: #디지털, #미술
2. 카테고리는 정해진 목록에서 선택해야 하며, 필요한 경우 다양한 카테고리를 조합할 수 있습니다.
3. 'items' 항목과 'store' 항목에는 각각 'item_id', 'tags', 'category' 필드가 반드시 포함되어야 합니다.
4. 모든 정보는 한국어로 제공되며, JSON 객체는 유효한 형식을 따라야 합니다.

카테고리 목록:

- 디지털 템플릿
- 사진 ∙ 영상
- 미술 ∙ 디자인
- 뷰티 ∙ 패션
- 요리 ∙ 베이킹
- 영화 ∙ 애니 ∙ 방송
- 음악 ∙ 춤 ∙ 엔터테인먼트
- 건강 ∙ 스포츠
- 게임 ∙ e스포츠
- 글쓰기
- 인테리어
- 타로 ∙ 사주 ∙ 관상
- 심리 ∙ 상담
- 교육 ∙ 학습
- IT ∙ 개발
- 자기계발 ∙ 커리어
- 금융 ∙ 재테크
- 청소년 ∙ 유아
- 반려동물
- 일상 ∙ 소통
- 추천 ∙ 리뷰
- 광고 ∙ 섭외
- ASMR
- 전자책
- 웹화보
- 기타


주어진 상점(store)과 상품(items) 정보를 바탕으로, 다음 형식에 맞게 태그와 카테고리를 생성하십시오.

예시 요청 형식:
```plaintext
{
  "store_id": 123,
  "items": [
    {
      "item_id": 1,
      "combined_contents": "디지털 아트 템플릿입니다. 고품질 디자인 자료를 제공합니다.",
      ...
    }
  ]
}

{
  "store": {
    "store_id": 123,
    "tags": "#디지털#아트#템플릿#웹화보",
    "category": "디지털 템플릿, 미술 ∙ 디자인, 웹화보"
  },
  "items": [
    {
      "item_id": 1,
      "tags": "#디지털#아트#템플릿",
      "category": "디지털 템플릿, 미술 ∙ 디자인"
    },
        {
      "item_id": 2,
      "tags": "#디지털#아트#템플릿#웹화보",
      "category": "디지털 템플릿, 미술 ∙ 디자인, 웹화보"
    }
  ]
}


                """,
                },
                {
                    "role": "user",
                    "content": f"상점정보 stores_id={store_id}, 아이템 정보 items={value}제공된 상점과 상품 정보를 바탕으로 태그들 만들고 카테고리를 생성해. 생성된 태그 정보는 JSON 형식으로 Store 따로 Item 따로 각각 반환되어야 하며, 주어진 규칙을 따라야 해.",
                },
            ],
            response_format={"type": "json_object"},
        )

        completion_data = json.loads(completion.choices[0].message.content)

        # 데이터 추가 로직 (가정: completion_data 처리가 이 위치에서 수행됨)
        store_data = completion_data["store"]
        items_data = completion_data["items"]
        # category_data = completion_data["category"]
        print(completion_data)
        print(f"store_data = {store_data}")
        print(f"items_data = {items_data}")
        # print(f"category= {category_data}")
        return True, store_data, items_data
    # , category_data

    except Exception as e:
        print(f"오류 발생: {e}")
        return False, None, None


# 파일 이름을 지정합니다.

In [99]:
store_file_name = "tag_output_stores.json"
items_file_name = "tag_output_items.json"
# category_file_name = "category_output.json"


In [100]:
# 각 스토어에 해당하는 아이템 그룹 확인
initialize_file(store_file_name)
initialize_file(items_file_name)
# initialize_file(category_file_name)


for store_id, group in grouped_items:
    print(f"Store ID: {store_id}")
    store = selected_stores_df[selected_stores_df['store_id'] == store_id]
    group.drop(['store_id'], axis=1, inplace=True)
    data_array = group.to_numpy()
    
    print(data_array)

    chunks = np.array_split(data_array, np.ceil(len(data_array) / 10))

    for chunk in chunks:
        attempt = 0
        success = False
        while attempt < 20 and not success:
            # tag_maker 함수가 스토어 정보와 해당 스토어의 DataFrame을 처리할 수 있어야 함
            success, store_data, items_data = tag_maker(store_id, chunk)
            append_json_list(store_data,store_file_name)
            append_json_list(items_data,items_file_name)
            # append_json_list(category_data,category_file_name)
            
            
            if not success:
                attempt += 1
                print(f"Attempt {attempt}: Failed to process store {store_id}. Retrying...")
        if not success:
            print(f"Failed to successfully process and save data for store {store_id} after 20 attempts.")


Store ID: 2
[[3
  'None안녕하세요, 그림 스피드페인팅 유튜버 노넴입니다 :)\n\n원하시는 컨셉에 맞춰 일러스트 아트워크를 제작해드릴게요. 제 채널에 방문하시면, 구매 전 보다 다양한 예시들을 참고하실 수 있습니다.\nNone']
 [4
  'None안녕하세요, 그림 스피드페인팅 유튜버 노넴입니다 :)\n\n원하시는 컨셉에 맞춰 일러스트 아트워크를 제작해드릴게요. 제 채널에 방문하시면, 구매 전 보다 다양한 예시들을 참고하실 수 있습니다.None']
 [5
  'None안녕하세요, 그림 스피드페인팅 유튜버 노넴입니다 :)\n\n원하시는 컨셉에 맞춰 일러스트 아트워크를 제작해드릴게요. 제 채널에 방문하시면, 구매 전 보다 다양한 예시들을 참고하실 수 있습니다.\nNone']
 [6
  'None안녕하세요, 그림 스피드페인팅 유튜버 노넴입니다 :)\n\n원하시는 컨셉에 맞춰 일러스트 아트워크를 제작해드릴게요. 제 채널에 방문하시면, 구매 전 보다 다양한 예시들을 참고하실 수 있습니다.\nNone']]
{'store': {'store_id': 2, 'tags': '#일러스트#아트#그림#유튜브', 'category': '미술 ∙ 디자인, 영상 ∙ 사진, 인터넷 방송'}, 'items': [{'item_id': 3, 'tags': '#일러스트#아트#그림', 'category': '미술 ∙ 디자인, 영상 ∙ 사진'}, {'item_id': 4, 'tags': '#일러스트#아트#그림', 'category': '미술 ∙ 디자인, 영상 ∙ 사진'}, {'item_id': 5, 'tags': '#일러스트#아트#그림', 'category': '미술 ∙ 디자인, 영상 ∙ 사진'}, {'item_id': 6, 'tags': '#일러스트#아트#그림', 'category': '미술 ∙ 디자인, 영상 ∙ 사진'}]}
store_data = {'store_id': 2, 'tags': '#일러스트#아트#그림#유튜브', 'category': '미술 ∙ 디자인, 영상 ∙ 사진,

In [97]:
# 예시 DataFrame 생성
group = pd.DataFrame({
    'item_id': [3, 4, 5, 6, 543],
    'store_id': [2, 2, 2, 2, 3],
    'tags': ['#그림 #스피드페인팅 #유튜버 #노넴 #컨셉', '#그림 #스피드페인팅 #유튜버 #노넴 #컨셉', '#그림 #스피드페인팅 #유튜버 #노넴 #컨셉', '#그림 #스피드페인팅 #유튜버 #노넴 #컨셉', '#관상 #상담 #특화 #키링 #부적 #맞춤']
})

# group에서 item_id와 태그 정보를 추출하여 API에 전달
for _, row in group.iterrows():
    item_id = row['item_id']
    tags = row['tags']
    # API 호출을 시뮬레이션 하는 부분 - 실제로는 API 호출 코드가 위치함
    print(f"Item ID: {item_id}, Tags: {tags}")
    # 예: API 호출 함수(api_call_function(item_id, tags))

Item ID: 3, Tags: #그림 #스피드페인팅 #유튜버 #노넴 #컨셉
Item ID: 4, Tags: #그림 #스피드페인팅 #유튜버 #노넴 #컨셉
Item ID: 5, Tags: #그림 #스피드페인팅 #유튜버 #노넴 #컨셉
Item ID: 6, Tags: #그림 #스피드페인팅 #유튜버 #노넴 #컨셉
Item ID: 543, Tags: #관상 #상담 #특화 #키링 #부적 #맞춤
